# **Imports and defining variables**

In [1]:
import pandas as pd
import re
import requests
import seaborn as sns
import matplotlib.pyplot as plt
from bs4 import BeautifulSoup
from random import randint
from time import sleep
from io import StringIO

In [ ]:
navigator = 'Microsoft Edge (Scrapping; This is my system)'
url_allbrands_homepage = 'https://www.auto-data.net/en/allbrands'
url = 'https://www.auto-data.net'

In [ ]:
html = requests.get(url_allbrands_homepage, headers={'User-Agent': navigator})
html

# **Scraping**

## Creating the soup and cleaning the information to get only text

In [18]:
soup = BeautifulSoup(html.text, 'html.parser')

In [19]:
brands = soup.find_all('a', {'class' : 'marki_blok'})
brands[0:5]

[<a class="marki_blok" href="/en/abarth-brand-200" title="Abarth - Technical Specs, Fuel consumption, Dimensions"><img alt="Abarth - Technical Specs, Fuel consumption, Dimensions" src="/img/logos/Abarth.png"/><strong>Abarth</strong></a>,
 <a class="marki_blok" href="/en/ac-brand-1" title="AC - Technical Specs, Fuel consumption, Dimensions"><img alt="AC - Technical Specs, Fuel consumption, Dimensions" src="/img/logos/AC.png"/><strong>AC</strong></a>,
 <a class="marki_blok" href="/en/acura-brand-6" title="Acura - Technical Specs, Fuel consumption, Dimensions"><img alt="Acura - Technical Specs, Fuel consumption, Dimensions" src="/img/logos/Acura.png"/><strong>Acura</strong></a>,
 <a class="marki_blok" href="/en/aiways-brand-301" title="Aiways - Technical Specs, Fuel consumption, Dimensions"><img alt="Aiways - Technical Specs, Fuel consumption, Dimensions" src="/img/logos/Aiways.png"/><strong>Aiways</strong></a>,
 <a class="marki_blok" href="/en/aixam-brand-255" title="Aixam - Technical Sp

In [20]:
#This loop is to get only the part to use in link ie whatever is after 'href='
brand_list = re.findall('href="(\S+)"',str(brands))
brand_list[0:5]

['/en/abarth-brand-200',
 '/en/ac-brand-1',
 '/en/acura-brand-6',
 '/en/aiways-brand-301',
 '/en/aixam-brand-255']

In [21]:
#Looping to remove the /en since the url already has it and removing it makes it so it will default to another language
brand_list_final = []
for i in range(len(brand_list)):
    brand_list_final += re.findall('en/(\S+)', brand_list[i])
brand_list_final[0:5]
#Starting to create dataframe for the links
df = pd.DataFrame(brand_list_final)
df['letter'] = df[0].apply(lambda x: x[0])
df['letter'].unique()

array(['a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm',
       'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'w', 'x', 'z'],
      dtype=object)

In [22]:
#Creating CSV files for each starting letter of the brand names so we can save it more often
dicto = {}
for letter in df['letter'].unique():
    a = df[df['letter'] == letter].drop(columns = 'letter')
    a.to_csv('../BEEV/letter_csvs/' + letter + '.csv')
    dicto[letter] = a

## Creating the loops for the actual scraping

In [23]:
#Looping to create a column with url brand names
url = 'https://www.auto-data.net/en/'
for csvs in dicto.values():
    csvs[0] = csvs[0].apply(lambda x: url + x)

In [24]:
#Renaming the column to make it easier to understand
for csvs in dicto.values():
    csvs.rename(columns={0 : 'brands_url'}, inplace = True)

In [25]:
#Dataframe with url for each brand
for letter, letter_csvs in dicto.items():
    letter_csvs.to_csv('../BEEV/letter_csvs/' + letter + '.csv')

In [26]:
#Function to get the models inside each brand
def model_of_each_brand(brand_url):
    models_list = []
    html2 = requests.get(brand_url, headers={'User-Agent': navigator})
    soup2 = BeautifulSoup(html2.text, 'html.parser')
    models = soup2.find_all('a', {'class' : 'modeli'}) 
    models_list_final = re.findall('en/(\S+)', str(models))
    return [x[:-1] for x in models_list_final]
brand_url = 'https://www.auto-data.net/en/abarth-brand-200'
model_of_each_brand(brand_url)

['abarth-124-spider-model-2152',
 'abarth-500-model-2872',
 'abarth-595-model-2149',
 'abarth-695-model-2150']

In [27]:
#Applying the function to get the models for each brand(displayed in lists inside the model_url column)
for csvs in dicto.values():
    csvs['models'] = csvs['brands_url'].apply(lambda x: model_of_each_brand(x))


In [28]:
#Saving to keep a column with models names
for letter, letter_csvs in dicto.items():
    letter_csvs.to_csv('../BEEV/letter_csvs/' + letter + '.csv')

In [29]:
#Loop to explode the models name and get 1 name per each line
for letter, letter_csvs in dicto.items():
    dicto[letter] = dicto[letter].explode('models')

In [30]:
dicto['a'].head()         #Just checking

brands_url                        models
0  https://www.auto-data.net/en/abarth-brand-200  abarth-124-spider-model-2152
0  https://www.auto-data.net/en/abarth-brand-200         abarth-500-model-2872
0  https://www.auto-data.net/en/abarth-brand-200         abarth-595-model-2149
0  https://www.auto-data.net/en/abarth-brand-200         abarth-695-model-2150
1        https://www.auto-data.net/en/ac-brand-1                ac-ace-model-1

In [31]:
#Loop to create a column with models_url
for csvs in dicto.values():
    csvs['models_url'] = csvs['models'].apply(lambda x: url + x)

In [32]:
#Saving the models_url column
for letter, letter_csvs in dicto.items():
    letter_csvs.to_csv('../BEEV/letter_csvs/' + letter + '.csv')

In [33]:
#Creating function to scrap the generation names for each models
def generation_of_each_model(model_url):
    gens_list = []
    html3 = requests.get(model_url, headers={'User-Agent': navigator})
    soup3 = BeautifulSoup(html3.text, 'html.parser')
    gens = soup3.find_all('a', {'class' : 'position'}) 
    gens_list_final = re.findall('en/(\S+)', str(gens))
    return [x[:-1] for x in gens_list_final]
model_url = 'https://www.auto-data.net/en/abarth-124-spider-model-2152'
generation_of_each_model(model_url)

['abarth-124-gt-generation-6774',
 'abarth-124-gt-generation-6774',
 'abarth-124-spider-generation-5004',
 'abarth-124-spider-generation-5004']

In [34]:
#Applying function to get the generation names for each models
for csvs in dicto.values():
    csvs['generations'] = csvs['models_url'].apply(lambda x: generation_of_each_model(x))

In [35]:
#Saving the generations columns
for letter, letter_csvs in dicto.items():
    letter_csvs.to_csv('../BEEV/letter_csvs/' + letter + '.csv')

In [36]:
#Loop to explode the generations names
for letter, letter_csvs in dicto.items():
    dicto[letter] = dicto[letter].explode('generations')

In [37]:
#Saving the exploded generations names
for letter, letter_csvs in dicto.items():
    letter_csvs.to_csv('../BEEV/letter_csvs/' + letter + '.csv')

In [38]:
#Dropping duplicates that were created
for letter, letter_csvs in dicto.items():
    dicto[letter].drop_duplicates(inplace = True)
    letter_csvs.to_csv('../BEEV/letter_csvs/' + letter + '.csv')

In [39]:
#Looping to create a column for the generations url
for csvs in dicto.values():
    csvs['generations_url'] = csvs['generations'].apply(lambda x: url + x)

In [40]:
#Saving the column with the generations urls
for letter, letter_csvs in dicto.items():
    letter_csvs.to_csv('../BEEV/letter_csvs/' + letter + '.csv')

In [41]:
#Creating a function to scrap for the modifications of each generation
def modifications_of_each_generation(gen_url):
    mods_list = []
    html4 = requests.get(gen_url, headers={'User-Agent': navigator})
    soup4 = BeautifulSoup(html4.text, 'html.parser')
    mods = soup4.find_all('table', {'class' : 'carlist'}) 
    gens_list_final = re.findall('en/(\S+)', str(mods))
    return [x[:-1] for x in gens_list_final]
gen_url = 'https://www.auto-data.net/en/alfa-romeo-mito-generation-363'
modifications_of_each_generation(gen_url)          

['alfa-romeo-mito-1.6-jtdm-120hp-16680',
 'alfa-romeo-mito-1.6-jtdm-120hp-16680',
 'alfa-romeo-mito-1.4-tb-multiair-170hp-44386',
 'alfa-romeo-mito-1.4-tb-multiair-170hp-44386',
 'alfa-romeo-mito-1.4-tb-155hp-16679',
 'alfa-romeo-mito-1.4-tb-155hp-16679',
 'alfa-romeo-mito-1.4-tb-multiair-135hp-tct-44377',
 'alfa-romeo-mito-1.4-tb-multiair-135hp-tct-44377',
 'alfa-romeo-mito-1.4-t-jet-120hp-16683',
 'alfa-romeo-mito-1.4-t-jet-120hp-16683',
 'alfa-romeo-mito-1.4-multiair-135hp-start-stop-16681',
 'alfa-romeo-mito-1.4-multiair-135hp-start-stop-16681',
 'alfa-romeo-mito-1.4-multiair-105hp-start-stop-16684',
 'alfa-romeo-mito-1.4-multiair-105hp-start-stop-16684',
 'alfa-romeo-mito-1.4-mpi-78hp-16682',
 'alfa-romeo-mito-1.4-mpi-78hp-16682',
 'alfa-romeo-mito-1.4-70hp-44378',
 'alfa-romeo-mito-1.4-70hp-44378',
 'alfa-romeo-mito-1.3-jtdm-90hp-40499',
 'alfa-romeo-mito-1.3-jtdm-90hp-40499',
 'alfa-romeo-mito-1.3-jtdm-eco-85hp-44387',
 'alfa-romeo-mito-1.3-jtdm-eco-85hp-44387',
 'alfa-romeo-mit

In [42]:
#Applying function to get the modifications names for each generation
for csvs in dicto.values():
    csvs['modifications'] = csvs['generations_url'].apply(lambda x: modifications_of_each_generation(x))

In [43]:
#Saving the mods column
for letter, letter_csvs in dicto.items():
    letter_csvs.to_csv('../BEEV/letter_csvs/' + letter + '.csv')

In [44]:
#Exploding the mods column to get one per row
for letter, letter_csvs in dicto.items():
    dicto[letter] = dicto[letter].explode('modifications')

In [45]:
#Saving the exploded generations names
for letter, letter_csvs in dicto.items():
    letter_csvs.to_csv('../BEEV/letter_csvs/' + letter + '.csv')

In [46]:
#Dropping duplicates that were created
for letter, letter_csvs in dicto.items():
    dicto[letter].drop_duplicates(inplace = True)
    letter_csvs.to_csv('../BEEV/letter_csvs/' + letter + '.csv')

In [47]:
#Loop to create a column for the mods url
for csvs in dicto.values():
    csvs['modifications_url'] = csvs['modifications'].apply(lambda x: url + str(x))

In [177]:
#Saving the column for the mods urls
for letter, letter_csvs in dicto.items():
    letter_csvs.to_csv('../BEEV/letter_csvs/' + letter + '.csv')

In [49]:
#This is the final loop to get the details for the cars
#specs = soup4.find_all('table', {'class' : 'cardetailsout car2'})

In [50]:
#Need to install this library to work
!pip install html5lib

## Final dataframe

In [222]:
#Creating the final function 

def specifications_of_each_car(mods_url):
    print(mods_url)
    if mods_url[-3:] == 'nan':
        return pd.DataFrame()
    else:
        specs = pd.read_html(mods_url)
        if len(specs)>=2:
            i=1
        elif len(specs)==1:
            return specs[0].drop_duplicates().T.reset_index(drop =True)
        else:
            return pd.DataFrame()
        specs = specs[i].drop_duplicates()
        #print(specs.T)
        #specs2 = specs[(specs['General information'] == 'Brand')
        #|(specs['General information'] == 'Model')
        #|(specs['General information'] == 'Generation')
        #|(specs['General information'] == 'Modification (Engine)')
        #|(specs['General information'] == 'CO2 emissions') 
        #|(specs['General information'] == 'Body type')
        #|(specs['General information'] == 'Fuel tank capacity')
        #|((specs['General information'] == 'Fuel consumption (economy) - combined') | (specs['General information'] == 'Fuel consumption (economy) - combined (NEDC)'))
        #|(specs['General information'] == 'Fuel Type')
        #|(specs['General information'] == 'Power')]
        specs.rename(columns = {'General information' : ''}, inplace = True)
        specs.set_index([''], inplace = True)
        #specs3 = specs2.T
        #specs3.reset_index(inplace = True)
        #specs3.drop(columns = ['index'], inplace = True)
        #specs3['Fuel tank(l)'] = specs3['Fuel tank capacity'].apply(lambda x : x.split(' ')[0])
        #specs3['Fuel consumption(l/100km)'] = specs3['Fuel consumption (economy) - combined'].apply(lambda x : x.split(' ')[0])
        #specs3['Power(Hp)'] = specs3['Power'].apply(lambda x: x.split(' ')[0])
        #specs3['Range (Km)'] = specs3[['Fuel tank(l)','Fuel consumption(l/100km)']].apply(lambda item: int(item[0])/float(item[1])*100,axis=1)
        #specs3.drop(columns = ['Fuel consumption (economy) - combined', 'Fuel tank capacity', 'Power'], inplace = True)
        return specs.T.reset_index(drop =True)
    

specifications_of_each_car('https://www.auto-data.net/en/abarth-124-gt-1.4-multiair-170hp-automatic-35172')

https://www.auto-data.net/en/abarth-124-gt-1.4-multiair-170hp-automatic-35172


Brand       Model Generation            Modification (Engine)  \
0  Abarth  124 Spider     124 GT  1.4 MultiAir (170 Hp) Automatic   

  Start of production     Powertrain Architecture Body type Seats Doors  \
0           2018 year  Internal Combustion engine  Roadster     2     2   

   Performance specs  ... Number of Gears (automatic transmission)  \
0  Performance specs  ...                                        6   

  Front suspension         Rear suspension      Front brakes Rear brakes  \
0  Double wishbone  Multi-link independent  Ventilated discs        Disc   

                Assisting systems             Steering type  \
0  ABS (Anti-lock braking system)  Steering rack and pinion   

      Power steering      Tires size Wheel rims size  
0  Electric Steering  205/45 R17 W84              17  

[1 rows x 61 columns]

In [218]:
#Creating the function to clean each DF because while scraping we do have duplicates and cannot concat with twice the same name for a column
def drop_dupli(df):
    return df.T.reset_index().drop_duplicates(inplace=False,subset = '').set_index('').T

In [284]:
#Creating an empty dataframe
#df = pd.DataFrame(columns = ['Brand', 'Model', 'Generation', 'Modification(Engine)','Body type', 'Fuel consumption (economy) - combined', 'CO2 emissions', 'Fuel type','Power','Fuel tank capacity', 'Fuel tank(l)', 'Fuel consumption(l/100km)', 'Power(Hp)','Range (km)'])
#df.reset_index()


In [182]:
#Testing for 'a' dataframe:
#for csvs in dicto['a']:
#    specifications_of_each_car(csvs['modifications_url'])
 #   df = pd.concat([df,specs3], ignore_index=True)

#Taking the shape to loop
#dicto['a']['modifications_url'].shape[0]
#dicto['b'].reset_index(inplace = True)
#global specs3   
#for i in range(0,dicto['a']['modifications_url'].shape[0]+1):
#    result = specifications_of_each_car(dicto['a']['modifications_url'].iloc[i])
#    print(i)
#    result = pd.concat([df,result], ignore_index=True)
#df.head()

In [282]:
#The for loop to build a DF in dataframe new column with apply specifications_of_each_car
#Then cleaning each DF with drop_dupli function with a condition to check if the DF is empty or not to avoid error message with no "" such column, 
#because in the scrap function depending of the web page we can scrap an empty DF
for letter in dicto.keys():
    dicto[letter]['dataframe'] = dicto[letter]['modifications_url'].apply(specifications_of_each_car)
    dicto[letter]['dataframe'] = dicto[letter]['dataframe'].apply(lambda item: drop_dupli(item) if item.shape[0]>0 else item)
    pd.concat([df for df in dicto[letter]['dataframe']]).to_csv(letter + '_scraped.csv',index=False)


https://www.auto-data.net/en/abarth-124-gt-1.4-multiair-170hp-automatic-35172
https://www.auto-data.net/en/abarth-124-gt-1.4-multiair-170hp-35171
https://www.auto-data.net/en/abarth-124-spider-1.4-multiair-170hp-automatic-24535
https://www.auto-data.net/en/abarth-124-spider-1.4-multiair-170hp-25192
https://www.auto-data.net/en/abarth-500c-1.4-t-jet-140hp-mta-42379
https://www.auto-data.net/en/abarth-500c-1.4-t-jet-135hp-42380
https://www.auto-data.net/en/abarth-500-1.4-t-jet-140hp-mta-42424
https://www.auto-data.net/en/abarth-500-1.4-t-jet-140hp-mta-42426
https://www.auto-data.net/en/abarth-500-1.4-t-jet-135hp-42425
https://www.auto-data.net/en/abarth-500-1.4-t-jet-135hp-42423
https://www.auto-data.net/en/abarth-595c-facelift-2016-turismo-1.4-t-jet-165hp-automatic-24780
https://www.auto-data.net/en/abarth-595c-facelift-2016-turismo-1.4-t-jet-165hp-25191
https://www.auto-data.net/en/abarth-595c-facelift-2016-pista-1.4-t-jet-160hp-automatic-34144
https://www.auto-data.net/en/abarth-595c-

https://www.auto-data.net/en/acura-mdx-iii-facelift-2017-3.5-v6-290hp-awd-automatic-32184
https://www.auto-data.net/en/acura-mdx-iii-facelift-2017-3.5-v6-290hp-automatic-32183
https://www.auto-data.net/en/acura-mdx-iii-facelift-2017-3.0-v6-321hp-hybrid-sh-awd-automatic-32166
https://www.auto-data.net/en/acura-mdx-iii-3.5-v6-290hp-awd-automatic-32191
https://www.auto-data.net/en/acura-mdx-iii-3.5-v6-290hp-automatic-32190
https://www.auto-data.net/en/acura-mdx-ii-3.7-v6-304hp-1080
https://www.auto-data.net/en/acura-mdx-3.5-i-v6-24v-263hp-1084
https://www.auto-data.net/en/acura-mdx-3.5-i-v6-24v-256hp-1083
https://www.auto-data.net/en/acura-mdx-3.5-i-v6-24v-243hp-1082
https://www.auto-data.net/en/acura-mdx-3.5-i-v6-24v-228hp-1081
https://www.auto-data.net/en/acura-nsx-ii-type-s-3.5-v6-600hp-hybrid-sh-awd-dct-44286
https://www.auto-data.net/en/acura-nsx-ii-3.5-v6-573hp-hybrid-sh-awd-30474
https://www.auto-data.net/en/acura-nsx-i-facelift-2002-3.2-v6-290hp-42139
https://www.auto-data.net/en/

https://www.auto-data.net/en/alfa-romeo-145-930-facelift-1997-1.6-t.-spark-120hp-1235
https://www.auto-data.net/en/alfa-romeo-145-930-facelift-1997-1.4-t.-spark-103hp-1233
https://www.auto-data.net/en/alfa-romeo-145-930-2.0-t.-spark-quadrifoglio-150hp-1242
https://www.auto-data.net/en/alfa-romeo-145-930-1.9-td-90hp-1240
https://www.auto-data.net/en/alfa-romeo-145-930-1.7-129hp-1236
https://www.auto-data.net/en/alfa-romeo-145-930-1.6-103hp-1234
https://www.auto-data.net/en/alfa-romeo-145-930-1.4-90hp-1232
https://www.auto-data.net/en/alfa-romeo-146-930-facelift-1999-2.0-ti-155hp-42162
https://www.auto-data.net/en/alfa-romeo-146-930-facelift-1999-1.9-jtd-105hp-16686
https://www.auto-data.net/en/alfa-romeo-146-930-facelift-1999-1.8-t.-spark-16v-144hp-42161
https://www.auto-data.net/en/alfa-romeo-146-930-facelift-1999-1.6-t.-spark-16v-120hp-42160
https://www.auto-data.net/en/alfa-romeo-146-930-facelift-1999-1.4-t.-spark-16v-103hp-42159
https://www.auto-data.net/en/alfa-romeo-146-930-faceli

https://www.auto-data.net/en/alfa-romeo-156-932-2.5-i-v6-24v-190hp-1491
https://www.auto-data.net/en/alfa-romeo-156-932-2.5-i-v6-24v-190hp-1490
https://www.auto-data.net/en/alfa-romeo-156-932-2.4-jtd-150hp-1489
https://www.auto-data.net/en/alfa-romeo-156-932-2.4-jtd-136hp-1488
https://www.auto-data.net/en/alfa-romeo-156-932-2.0-jts-165hp-1487
https://www.auto-data.net/en/alfa-romeo-156-932-2.0-i-16v-t.spark-155hp-1486
https://www.auto-data.net/en/alfa-romeo-156-932-1.9-jtd-115hp-1485
https://www.auto-data.net/en/alfa-romeo-156-932-1.9-jtd-105hp-1484
https://www.auto-data.net/en/alfa-romeo-156-932-1.8-16v-t.s.-144hp-1483
https://www.auto-data.net/en/alfa-romeo-156-932-1.6-16v-t.s.-120hp-1482
https://www.auto-data.net/en/alfa-romeo-159-sportwagon-3.2-jts-v6-260hp-q4-q-tronic-1536
https://www.auto-data.net/en/alfa-romeo-159-sportwagon-3.2-jts-v6-260hp-q4-1535
https://www.auto-data.net/en/alfa-romeo-159-sportwagon-3.2-jts-v6-260hp-41197
https://www.auto-data.net/en/alfa-romeo-159-sportwago

https://www.auto-data.net/en/alfa-romeo-33-907a-1.5-105hp-1377
https://www.auto-data.net/en/alfa-romeo-33-907a-1.4-i.e.-90hp-1376
https://www.auto-data.net/en/alfa-romeo-33-907a-1.4-i.e.-88hp-1375
https://www.auto-data.net/en/alfa-romeo-33-sport-wagon-905a-1.7-i.e.-105hp-4x4-1421
https://www.auto-data.net/en/alfa-romeo-33-sport-wagon-905a-1.7-i.e.-105hp-1420
https://www.auto-data.net/en/alfa-romeo-33-sport-wagon-905a-1.7-118hp-1419
https://www.auto-data.net/en/alfa-romeo-33-sport-wagon-905a-1.5-90hp-4x4-1417
https://www.auto-data.net/en/alfa-romeo-33-sport-wagon-905a-1.5-90hp-1415
https://www.auto-data.net/en/alfa-romeo-33-sport-wagon-905a-1.5-105hp-4x4-1418
https://www.auto-data.net/en/alfa-romeo-33-sport-wagon-905a-1.5-105hp-1414
https://www.auto-data.net/en/alfa-romeo-33-sport-wagon-905a-1.5-102hp-4x4-1416
https://www.auto-data.net/en/alfa-romeo-33-sport-wagon-905a-1.5-102hp-1413
https://www.auto-data.net/en/alfa-romeo-33-905-1.8-td-73hp-1412
https://www.auto-data.net/en/alfa-romeo-

...

https://www.auto-data.net/en/volvo-v60-i-2013-facelift-2.0-t5-245hp-automatic-21747
https://www.auto-data.net/en/volvo-v60-i-2013-facelift-2.0-t5-240hp-automatic-18399
https://www.auto-data.net/en/volvo-v60-i-2013-facelift-2.0-t4-190hp-automatic-21757
https://www.auto-data.net/en/volvo-v60-i-2013-facelift-2.0-t4-190hp-21756
https://www.auto-data.net/en/volvo-v60-i-2013-facelift-2.0-t3-152hp-21754
https://www.auto-data.net/en/volvo-v60-i-2013-facelift-2.0-d5-225hp-automatic-21764
https://www.auto-data.net/en/volvo-v60-i-2013-facelift-2.0-d4-190hp-automatic-21762
https://www.auto-data.net/en/volvo-v60-i-2013-facelift-2.0-d4-190hp-21733
https://www.auto-data.net/en/volvo-v60-i-2013-facelift-2.0-d4-181hp-automatic-21748
https://www.auto-data.net/en/volvo-v60-i-2013-facelift-2.0-d4-181hp-21724
https://www.auto-data.net/en/volvo-v60-i-2013-facelift-2.0-d4-163hp-start-stop-18391
https://www.auto-data.net/en/volvo-v60-i-2013-facelift-2.0-d4-163hp-automatic-start-stop-18392
https://www.auto-dat

https://www.auto-data.net/en/volvo-v70-iii-1.6-t4f-180hp-ethanol-24712
https://www.auto-data.net/en/volvo-v70-iii-1.6-t4-180hp-automatic-25337
https://www.auto-data.net/en/volvo-v70-iii-1.6-t4-180hp-24650
https://www.auto-data.net/en/volvo-v70-iii-1.6-d-drive-109hp-24761
https://www.auto-data.net/en/volvo-v70-ii-facelift-2004-2.5t-210hp-geartronic-42644
https://www.auto-data.net/en/volvo-v70-ii-facelift-2004-2.5t-210hp-awd-geartronic-42647
https://www.auto-data.net/en/volvo-v70-ii-facelift-2004-2.5t-210hp-awd-42646
https://www.auto-data.net/en/volvo-v70-ii-facelift-2004-2.5t-210hp-42643
https://www.auto-data.net/en/volvo-v70-ii-facelift-2004-2.4i-20v-t5-260hp-automatic-25879
https://www.auto-data.net/en/volvo-v70-ii-facelift-2004-2.4i-20v-t5-260hp-9245
https://www.auto-data.net/en/volvo-v70-ii-facelift-2004-2.4d-163hp-geartronic-42649
https://www.auto-data.net/en/volvo-v70-ii-facelift-2004-2.4d-163hp-42648
https://www.auto-data.net/en/volvo-v70-ii-facelift-2004-2.4d-126hp-42645
https:/

https://www.auto-data.net/en/volvo-v90-combi-2016-2.0-t6-310hp-awd-automatic-32888
https://www.auto-data.net/en/volvo-v90-combi-2016-2.0-t5-254hp-automatic-22753
https://www.auto-data.net/en/volvo-v90-combi-2016-2.0-t5-250hp-automatic-36306
https://www.auto-data.net/en/volvo-v90-combi-2016-2.0-t5-250hp-automatic-32886
https://www.auto-data.net/en/volvo-v90-combi-2016-2.0-t4-190hp-automatic-36280
https://www.auto-data.net/en/volvo-v90-combi-2016-2.0-t4-190hp-automatic-32885
https://www.auto-data.net/en/volvo-v90-combi-2016-2.0-d5-235hp-awd-automatic-36299
https://www.auto-data.net/en/volvo-v90-combi-2016-2.0-d5-235hp-awd-automatic-22762
https://www.auto-data.net/en/volvo-v90-combi-2016-2.0-d4-190hp-awd-automatic-36300
https://www.auto-data.net/en/volvo-v90-combi-2016-2.0-d4-190hp-awd-automatic-27546
https://www.auto-data.net/en/volvo-v90-combi-2016-2.0-d4-190hp-automatic-36301
https://www.auto-data.net/en/volvo-v90-combi-2016-2.0-d4-190hp-automatic-22751
https://www.auto-data.net/en/vol

https://www.auto-data.net/en/volvo-xc60-i-2013-facelift-2.0-d3-150hp-automatic-21803
https://www.auto-data.net/en/volvo-xc60-i-2013-facelift-2.0-d3-150hp-21802
https://www.auto-data.net/en/volvo-xc60-i-2013-facelift-2.0-d3-136hp-start-stop-18377
https://www.auto-data.net/en/volvo-xc60-i-2013-facelift-2.0-d3-136hp-automatic-18378
https://www.auto-data.net/en/volvo-xc60-i-3.2-243hp-awd-17601
https://www.auto-data.net/en/volvo-xc60-i-3.2-238hp-awd-17159
https://www.auto-data.net/en/volvo-xc60-i-3.0-t6-304hp-awd-17600
https://www.auto-data.net/en/volvo-xc60-i-3.0-t6-285hp-awd-geartronic-9390
https://www.auto-data.net/en/volvo-xc60-i-3.0-t6-285hp-awd-17165
https://www.auto-data.net/en/volvo-xc60-i-2.4-d5-215hp-awd-17598
https://www.auto-data.net/en/volvo-xc60-i-2.4-d5-215hp-17597
https://www.auto-data.net/en/volvo-xc60-i-2.4-d5-205hp-awd-automatic-17163
https://www.auto-data.net/en/volvo-xc60-i-2.4-d5-205hp-awd-17164
https://www.auto-data.net/en/volvo-xc60-i-2.4-d5-185hp-awd-geartronic-9387

https://www.auto-data.net/en/volvo-xc90-facelift-2007-2.4-d3-163hp-automatic-21818
https://www.auto-data.net/en/volvo-xc90-3.2-243hp-awd-17612
https://www.auto-data.net/en/volvo-xc90-2.9-t6-272hp-9530
https://www.auto-data.net/en/volvo-xc90-2.8-24v-272hp-9529
https://www.auto-data.net/en/volvo-xc90-2.5-t-20v-210hp-automatic-24588
https://www.auto-data.net/en/volvo-xc90-2.5-t-20v-210hp-9526
https://www.auto-data.net/en/volvo-xc90-2.4-tdi-163hp-automatic-9523
https://www.auto-data.net/en/volvo-xc90-2.4-d3-163hp-17610
https://www.auto-data.net/en/vuhl-05-rr-2.3-385hp-automatic-32083
https://www.auto-data.net/en/vuhl-05-2.0-289hp-32082
https://www.auto-data.net/en/vw-porsche-914-2.0-110hp-10145
https://www.auto-data.net/en/vw-porsche-914-2.0-100hp-10148
https://www.auto-data.net/en/vw-porsche-914-1.8-86hp-10147
https://www.auto-data.net/en/vw-porsche-914-1.7-80hp-10146
https://www.auto-data.net/en/nan
https://www.auto-data.net/en/w-motors-fenyr-supersport-4.0-900hp-automatic-32100
https://

In [181]:
#test1 = specifications_of_each_car(dicto['a']['modifications_url'][0])
#test2 = specifications_of_each_car(dicto['a']['modifications_url'][1])
#print(test1,test2)
#type(test1)
#tttt = pd.concat([tttt,test2], ignore_index=True)
#tttt
#df = pd.concat([df,specs3], ignore_index=True)

In [124]:
# #This is the dataframe with all the information we want
# page4 = 'https://www.auto-data.net/en/alfa-romeo-mito-1.6-jtdm-120hp-16680'
# what = pd.read_html(page4)[1]  
# what

# what2 = what[(what['General information'] == 'Brand')
# |(what['General information'] == 'Model')
# |(what['General information'] == 'Generation')
# |(what['General information'] == 'Modification (Engine)')
# |(what['General information'] == 'CO2 emissions') 
# |(what['General information'] == 'Body type')
# |(what['General information'] == 'Fuel tank capacity')
# |(what['General information'] == 'Fuel consumption (economy) - combined')
# |(what['General information'] == 'Fuel Type')
# |(what['General information'] == 'Power')]
# what2.index = what2['General information']
# what3 = what2.T
# what3.drop(axis = 0, labels = 'General information', inplace = True)
# what3['Fuel tank(l)'] = what3['Fuel tank capacity'].apply(lambda x : x.split(' ')[0])
# what3['Fuel consumption(l/100km)'] = what3['Fuel consumption (economy) - combined'].apply(lambda x : x.split(' ')[0])
# what3['Power(Hp)'] = what3['Power'].apply(lambda x: x.split(' ')[0])
# what3['Range (Km)'] = what3[['Fuel tank(l)','Fuel consumption(l/100km)']].apply(lambda item: int(item[0])/float(item[1])*100,axis=1)

# what4 = what3
# what4.drop(columns = ['Fuel consumption (economy) - combined', 'Fuel tank capacity'], inplace = True)
# what4                               #We need to remove this General information column still

In [2]:
#To re-build the dicto from letter.csv file already saved
letters = ['a','b','c','d','e','f','g','h','i','j','k','l','m','n','o','p','q','r','s','t','u','v','w','x','z']
dicto = {letter : pd.read_csv("../BEEV/letter_csvs/"+ letter +".csv",index_col=None) for letter in letters}


{'a':       Unnamed: 0                                         brands_url  \
 0              0      https://www.auto-data.net/en/abarth-brand-200   
 1              1      https://www.auto-data.net/en/abarth-brand-200   
 2              2      https://www.auto-data.net/en/abarth-brand-200   
 3              3      https://www.auto-data.net/en/abarth-brand-200   
 4              4      https://www.auto-data.net/en/abarth-brand-200   
 ...          ...                                                ...   
 3870        3870  https://www.auto-data.net/en/autobianchi-brand-51   
 3871        3871  https://www.auto-data.net/en/autobianchi-brand-51   
 3872        3872  https://www.auto-data.net/en/autobianchi-brand-51   
 3873        3873  https://www.auto-data.net/en/autobianchi-brand-51   
 3874        3874  https://www.auto-data.net/en/autobianchi-brand-51   
 
                             models  \
 0     abarth-124-spider-model-2152   
 1     abarth-124-spider-model-2152   
 2     abart

In [ ]:
################## Debugging code part

In [277]:
#df = dicto['a']['dataframe'][0]
#for i in range(1,dicto['a']['dataframe'].shape[0]+1):
 #   df = pd.concat(df,dicto['a']['dataframe'][i])
#df
#pd.concat([dicto['a']['dataframe'][0].reset_index(drop = True),dicto['a']['dataframe'][1]].reset_index(drop = True))
testdf1 = dicto['a']['dataframe'][0]#.reset_index(drop = True)
testdf2 = dicto['a']['dataframe'][10]#.reset_index(drop = True)
#pd.concat([testdf1,testdf2],ignore_index = True,axis = 0).reindex(testdf1.index)
#testdf1.append(testdf2)
result = pd.concat([df for df in dicto['a']['dataframe']])#.iloc[:115]])#pd.concat([testdf1, testdf2])#, ignore_index=True, sort=False, axis = 0)
result

Brand       Model  Generation            Modification (Engine)  \
0        Abarth  124 Spider      124 GT  1.4 MultiAir (170 Hp) Automatic   
0        Abarth  124 Spider      124 GT            1.4 MultiAir (170 Hp)   
0        Abarth  124 Spider  124 Spider  1.4 MultiAir (170 Hp) Automatic   
0        Abarth  124 Spider  124 Spider            1.4 MultiAir (170 Hp)   
0        Abarth         500        500C           1.4 T-Jet (140 Hp) MTA   
..          ...         ...         ...                              ...   
0   Autobianchi       A 112       A 112               1.0 Abarth (58 Hp)   
0   Autobianchi       A 112       A 112               0.9 Junior (42 Hp)   
0   Autobianchi       A 112       A 112                    0.9 E (47 Hp)   
0   Autobianchi       A 112       A 112                      0.9 (45 Hp)   
0   Autobianchi       A 112       A 112                      0.9 (44 Hp)   

   Start of production     Powertrain Architecture  Body type Seats Doors  \
0            2018 year  Internal Combustion engine   Roadster     2     2   
0            2018 year  Internal Combustion engine   Roadster     2     2   
0            2016 year  Internal Combustion engine  Cabriolet     2     2   
0            2016 year  Internal Combustion engine  Cabriolet     2     2   
0            2010 year  Internal Combustion engine  Cabriolet     4     2   
..                 ...                         ...        ...   ...   ...   
0            1971 year  Internal Combustion engine  Hatchback   NaN   NaN   
0            1975 year  Internal Combustion engine  Hatchback   NaN   NaN   
0            1973 year  Internal Combustion engine  Hatchback   NaN   NaN   
0            1976 year  Internal Combustion engine  Hatchback   NaN   NaN   
0            1969 year  Internal Combustion engine  Hatchback   NaN   NaN   

    Performance specs  ... CO2 emissions (CNG) (NEDC)  \
0   Performance specs  ...                        NaN   
0   Performance specs  ...                        NaN   
0   Performance specs  ...                        NaN   
0   Performance specs  ...                        NaN   
0   Performance specs  ...                        NaN   
..                ...  ...                        ...   
0   Performance specs  ...                        NaN   
0   Performance specs  ...                        NaN   
0   Performance specs  ...                        NaN   
0   Performance specs  ...                        NaN   
0   Performance specs  ...                        NaN   

   All-electric range (NEDC) Net (usable) battery capacity Battery technology  \
0                        NaN                           NaN                NaN   
0                        NaN                           NaN                NaN   
0                        NaN                           NaN                NaN   
0                        NaN                           NaN                NaN   
0                        NaN                           NaN                NaN   
..                       ...                           ...                ...   
0                        NaN                           NaN                NaN   
0                        NaN                           NaN                NaN   
0                        NaN                           NaN                NaN   
0                        NaN                           NaN                NaN   
0                        NaN                           NaN                NaN   

   Acceleration 0 - 200 km/h Recuperation output  \
0                        NaN                 NaN   
0                        NaN                 NaN   
0                        NaN                 NaN   
0                        NaN                 NaN   
0                        NaN                 NaN   
..                       ...                 ...   
0                        NaN                 NaN   
0                        NaN                 NaN   
0                        NaN                 N

In [72]:
print(len(dicto['a']['dataframe'][10].reset_index(drop =True).columns))
#dicto['a']['dataframe'][10].columns

70


In [73]:
print(len(dicto['a']['dataframe'][0].reset_index(drop =True).columns))
#dicto['a']['dataframe'][0].columns

61


In [228]:
for values in dicto['a']['dataframe'][114].reset_index(drop =True).columns:
    if values not in dicto['a']['dataframe'][115].reset_index(drop =True).columns:
        print(values)

Electric cars and hybrids specs
Electric motor 1
Electric motor power
Electric motor Torque
Electric motor 2
Electric motor power
Electric motor Torque
Electric motor 3
System power
System torque
Internal combustion engine specs
Drivetrain Architecture


In [223]:
dicto['a']['dataframe'][10].reset_index(drop =True)#['(adsbygoogle = window.adsbygoogle || []).push({});']

Brand Model            Generation                 Modification (Engine)  \
0  Abarth   595  595C (facelift 2016)  Turismo 1.4 T-Jet (165 Hp) Automatic   

  Start of production     Powertrain Architecture  Body type Seats Doors  \
0           2016 year  Internal Combustion engine  Cabriolet     4     3   

   Performance specs  ... Number of Gears (automatic transmission)  \
0  Performance specs  ...                                        5   

             Front suspension                Rear suspension  \
0  Independent type McPherson  Semi-independent, coil spring   

               Front brakes               Rear brakes  \
0  Ventilated discs, 284 mm  Ventilated discs, 240 mm   

                Assisting systems             Steering type  \
0  ABS (Anti-lock braking system)  Steering rack and pinion   

      Power steering  Tires size Wheel rims size  
0  Electric Steering  205/40 R17              17  

[1 rows x 67 columns]

In [278]:
for letter in dicto.keys():
    #dicto['a']['dataframe'] = dicto['a']['modifications_url'].apply(specifications_of_each_car)
    #dicto['a']['dataframe'] = dicto['a']['dataframe'].apply(lambda item: drop_dupli(item) if item.shape[0]>0 else item)
    pd.concat([df for df in dicto['a']['dataframe']]).to_csv(letter + '_scraped.csv',index=False)
    #df_car = pd.concat(list(dicto[letter]['dataframe']),ignore_index=True)
    #pd.concat(list(dicto[letter]['dataframe']),ignore_index=True,join = 'inner').to_csv(letter + '_scraped.csv',index=False)
    #df_car.to_csv(letter + '_scraped.csv',index=False)

KeyboardInterrupt: 

In [135]:
#dicto['a']['dataframe'][115].T[dicto['a']['dataframe'][115].T.duplicated() == True]
dicto['a']['dataframe'].iloc[114]#.columns

Brand Model               Generation  \
0  Acura   MDX  MDX III (facelift 2017)   

                     Modification (Engine) Start of production  \
0  3.0 V6 (321 Hp) Hybrid SH-AWD Automatic           2017 year   

  End of production              Powertrain Architecture Body type Seats  \
0         2020 year  FHEV (Full Hybrid Electric Vehicle)       SUV   6-7   

  Doors  ... Number of Gears (automatic transmission)  \
0     5  ...                                    7 DCT   

                                 Front suspension         Rear suspension  \
0  Independent, Spring McPherson, with stabilizer  Multi-link independent   

       Front brakes Rear brakes               Assisting systems  \
0  Ventilated discs        Disc  ABS (Anti-lock braking system)   

              Steering type     Power steering              Tires size  \
0  Steering rack and pinion  Electric Steering  245/60 R18; 245/50 R20   

    Wheel rims size  
0  8J x 18; 8J x 20  

[1 rows x 73 columns]

In [177]:
len(dicto['a']['dataframe'].iloc[114].columns)
#len(set(dicto['a']['dataframe'].iloc[114].columns))

73

In [ ]:
#pd.concat([dicto['a']['dataframe'].iloc[114],dicto['a']['dataframe'].iloc[115]])

In [90]:
[print(df) for df in dicto['a']['dataframe'].iloc[:10]]

                        Brand       Model Generation  \
General information.1  Abarth  124 Spider     124 GT   

                                 Modification (Engine) Start of production  \
General information.1  1.4 MultiAir (170 Hp) Automatic           2018 year   

                          Powertrain Architecture Body type Seats  \
General information.1  Internal Combustion engine  Roadster     2   

                       Performance specs  \
General information.1  Performance specs   

                                     Fuel consumption (economy) - urban  ...  \
General information.1  9.1 l/100 km  25.85 US mpg31.04 UK mpg10.99 km/l  ...   

                      Number of Gears (automatic transmission)  \
General information.1                                        6   

                      Front suspension         Rear suspension  \
General information.1  Double wishbone  Multi-link independent   

                           Front brakes Rear brakes  \
General information.

[None, None, None, None, None, None, None, None, None, None]

In [188]:
dicto['a']['dataframe'].iloc[114].T.reset_index()[""][dicto['a']['dataframe'].iloc[114].T.reset_index()[""].duplicated() == True]#.drop_duplicates().set_index("")


22     Electric motor power
23    Electric motor Torque
24          Engine location
32          Engine location
Name: , dtype: object

In [206]:
test = dicto['a']['dataframe'].iloc[114].T.reset_index()

In [207]:
test.drop_duplicates(inplace=True,subset = '')

In [210]:
test

0
0                   Brand                                    Acura
1                   Model                                      MDX
2              Generation                  MDX III (facelift 2017)
3   Modification (Engine)  3.0 V6 (321 Hp) Hybrid SH-AWD Automatic
4     Start of production                                2017 year
..                    ...                                      ...
68      Assisting systems           ABS (Anti-lock braking system)
69          Steering type                 Steering rack and pinion
70         Power steering                        Electric Steering
71             Tires size                   245/60 R18; 245/50 R20
72        Wheel rims size                         8J x 18; 8J x 20

[69 rows x 2 columns]

In [212]:
test.set_index('').T

Brand Model               Generation  \
0  Acura   MDX  MDX III (facelift 2017)   

                     Modification (Engine) Start of production  \
0  3.0 V6 (321 Hp) Hybrid SH-AWD Automatic           2017 year   

  End of production              Powertrain Architecture Body type Seats  \
0         2020 year  FHEV (Full Hybrid Electric Vehicle)       SUV   6-7   

  Doors  ... Number of Gears (automatic transmission)  \
0     5  ...                                    7 DCT   

                                 Front suspension         Rear suspension  \
0  Independent, Spring McPherson, with stabilizer  Multi-link independent   

       Front brakes Rear brakes               Assisting systems  \
0  Ventilated discs        Disc  ABS (Anti-lock braking system)   

              Steering type     Power steering              Tires size  \
0  Steering rack and pinion  Electric Steering  245/60 R18; 245/50 R20   

    Wheel rims size  
0  8J x 18; 8J x 20  

[1 rows x 69 columns]

In [250]:
drop_dupli(dicto['a']['dataframe'][0])

Brand       Model Generation            Modification (Engine)  \
0  Abarth  124 Spider     124 GT  1.4 MultiAir (170 Hp) Automatic   

  Start of production     Powertrain Architecture Body type Seats Doors  \
0           2018 year  Internal Combustion engine  Roadster     2     2   

   Performance specs  ... Number of Gears (automatic transmission)  \
0  Performance specs  ...                                        6   

  Front suspension         Rear suspension      Front brakes Rear brakes  \
0  Double wishbone  Multi-link independent  Ventilated discs        Disc   

                Assisting systems             Steering type  \
0  ABS (Anti-lock braking system)  Steering rack and pinion   

      Power steering      Tires size Wheel rims size  
0  Electric Steering  205/45 R17 W84              17  

[1 rows x 61 columns]

In [248]:
dicto['a']['dataframe'].iloc[116]

Brand Model Generation      Modification (Engine) Start of production  \
0  Acura   MDX    MDX III  3.5 V6 (290 Hp) Automatic           2013 year   

  End of production     Powertrain Architecture Body type Seats Doors  ...  \
0         2016 year  Internal Combustion engine       SUV     7     5  ...   

  Number of Gears (automatic transmission)  \
0                             6 SportShift   

                                 Front suspension         Rear suspension  \
0  Independent, Spring McPherson, with stabilizer  Multi-link independent   

       Front brakes Rear brakes               Assisting systems  \
0  Ventilated discs        Disc  ABS (Anti-lock braking system)   

              Steering type     Power steering              Tires size  \
0  Steering rack and pinion  Electric Steering  245/60 R18; 245/55 R19   

    Wheel rims size  
0  8J x 18; 8J x 19  

[1 rows x 65 columns]

In [261]:
#dicto['a']['dataframe'] = dicto['a']['dataframe'].apply(lambda item: drop_dupli(item))
#for i in range(dicto['a']['dataframe'].shape[0]):
 #   if dicto['a']['dataframe'][i].shape[0]>0:
  #      dicto['a']['dataframe'][i] = drop_dupli(dicto['a']['dataframe'][i])
   # else: pass
    #print(i)

/var/folders/zp/g__9z3d17bl6nkkpnxb0p46r0000gn/T/ipykernel_2818/2173370025.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dicto['a']['dataframe'][i] = drop_dupli(dicto['a']['dataframe'][i])


0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

1951
1952
1953
1954
1955
1956
1957
1958
1959
1960
1961
1962
1963
1964
1965
1966
1967
1968
1969
1970
1971
1972
1973
1974
1975
1976
1977
1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989
1990
1991
1992
1993
1994
1995
1996
1997
1998
1999
2000
2001
2002
2003
2004
2005
2006
2007
2008
2009
2010
2011
2012
2013
2014
2015
2016
2017
2018
2019
2020
2021
2022
2023
2024
2025
2026
2027
2028
2029
2030
2031
2032
2033
2034
2035
2036
2037
2038
2039
2040
2041
2042
2043
2044
2045
2046
2047
2048
2049
2050
2051
2052
2053
2054
2055
2056
2057
2058
2059
2060
2061
2062
2063
2064
2065
2066
2067
2068
2069
2070
2071
2072
2073
2074
2075
2076
2077
2078
2079
2080
2081
2082
2083
2084
2085
2086
2087
2088
2089
2090
2091
2092
2093
2094
2095
2096
2097
2098
2099
2100
2101
2102
2103
2104
2105
2106
2107
2108
2109
2110
2111
2112
2113
2114
2115
2116
2117
2118
2119
2120
2121
2122
2123
2124
2125
2126
2127
2128
2129
2130
2131
2132
2133
2134
2135
2136
2137
2138
2139
2140
2141
2142
2143
2144
2145
2146
2147
2148
2149
2150


3618
3619
3620
3621
3622
3623
3624
3625
3626
3627
3628
3629
3630
3631
3632
3633
3634
3635
3636
3637
3638
3639
3640
3641
3642
3643
3644
3645
3646
3647
3648
3649
3650
3651
3652
3653
3654
3655
3656
3657
3658
3659
3660
3661
3662
3663
3664
3665
3666
3667
3668
3669
3670
3671
3672
3673
3674
3675
3676
3677
3678
3679
3680
3681
3682
3683
3684
3685
3686
3687
3688
3689
3690
3691
3692
3693
3694
3695
3696
3697
3698
3699
3700
3701
3702
3703
3704
3705
3706
3707
3708
3709
3710
3711
3712
3713
3714
3715
3716
3717
3718
3719
3720
3721
3722
3723
3724
3725
3726
3727
3728
3729
3730
3731
3732
3733
3734
3735
3736
3737
3738
3739
3740
3741
3742
3743
3744
3745
3746
3747
3748
3749
3750
3751
3752
3753
3754
3755
3756
3757
3758
3759
3760
3761
3762
3763
3764
3765
3766
3767
3768
3769
3770
3771
3772
3773
3774
3775
3776
3777
3778
3779
3780
3781
3782
3783
3784
3785
3786
3787
3788
3789
3790
3791
3792
3793
3794
3795
3796
3797
3798
3799
3800
3801
3802
3803
3804
3805
3806
3807
3808
3809
3810
3811
3812
3813
3814
3815
3816
3817


In [254]:
dicto['a']['dataframe'][53]

Brand Model Generation  Modification (Engine) Start of production  \
0    AC   ACE     Ace II  2.9 i V6 24V (195 Hp)           1992 year   

  End of production     Powertrain Architecture  Body type  Performance specs  \
0         1996 year  Internal Combustion engine  Cabriolet  Performance specs   

           Fuel Type  Engine specs   Power           Engine aspiration  \
0  Petrol (Gasoline)  Engine specs  195 Hp  Naturally aspirated engine   

  (adsbygoogle = window.adsbygoogle || []).push({});  \
0  (adsbygoogle = window.adsbygoogle || []).push(...   

   Drivetrain, brakes and suspension specs Wheel rims size  
0  Drivetrain, brakes and suspension specs               4

In [259]:
dicto['a']['dataframe'][54].shape

(0, 0)

In [279]:
pd.read_csv("a_scraped.csv")


Brand       Model  Generation            Modification (Engine)  \
0          Abarth  124 Spider      124 GT  1.4 MultiAir (170 Hp) Automatic   
1          Abarth  124 Spider      124 GT            1.4 MultiAir (170 Hp)   
2          Abarth  124 Spider  124 Spider  1.4 MultiAir (170 Hp) Automatic   
3          Abarth  124 Spider  124 Spider            1.4 MultiAir (170 Hp)   
4          Abarth         500        500C           1.4 T-Jet (140 Hp) MTA   
...           ...         ...         ...                              ...   
3856  Autobianchi       A 112       A 112               1.0 Abarth (58 Hp)   
3857  Autobianchi       A 112       A 112               0.9 Junior (42 Hp)   
3858  Autobianchi       A 112       A 112                    0.9 E (47 Hp)   
3859  Autobianchi       A 112       A 112                      0.9 (45 Hp)   
3860  Autobianchi       A 112       A 112                      0.9 (44 Hp)   

     Start of production     Powertrain Architecture  Body type Seats Doors  \
0              2018 year  Internal Combustion engine   Roadster     2     2   
1              2018 year  Internal Combustion engine   Roadster     2     2   
2              2016 year  Internal Combustion engine  Cabriolet     2     2   
3              2016 year  Internal Combustion engine  Cabriolet     2     2   
4              2010 year  Internal Combustion engine  Cabriolet     4     2   
...                  ...                         ...        ...   ...   ...   
3856           1971 year  Internal Combustion engine  Hatchback   NaN   NaN   
3857           1975 year  Internal Combustion engine  Hatchback   NaN   NaN   
3858           1973 year  Internal Combustion engine  Hatchback   NaN   NaN   
3859           1976 year  Internal Combustion engine  Hatchback   NaN   NaN   
3860           1969 year  Internal Combustion engine  Hatchback   NaN   NaN   

      Performance specs  ... CO2 emissions (CNG) (NEDC)  \
0     Performance specs  ...                        NaN   
1     Performance specs  ...                        NaN   
2     Performance specs  ...                        NaN   
3     Performance specs  ...                        NaN   
4     Performance specs  ...                        NaN   
...                 ...  ...                        ...   
3856  Performance specs  ...                        NaN   
3857  Performance specs  ...                        NaN   
3858  Performance specs  ...                        NaN   
3859  Performance specs  ...                        NaN   
3860  Performance specs  ...                        NaN   

     All-electric range (NEDC) Net (usable) battery capacity  \
0                          NaN                           NaN   
1                          NaN                           NaN   
2                          NaN                           NaN   
3                          NaN                           NaN   
4                          NaN                           NaN   
...                        ...                           ...   
3856                       NaN                           NaN   
3857                       NaN                           NaN   
3858                       NaN                           NaN   
3859                       NaN                           NaN   
3860                       NaN                           NaN   

     Battery technology Acceleration 0 - 200 km/h Recuperation output  \
0                   NaN                       NaN                 NaN   
1                   NaN                       NaN                 NaN   
2                   NaN                       NaN                 NaN   
3                   NaN                       NaN                 NaN   
4                   NaN                       NaN                 NaN   
...                 ...                       ...                 ...   
3856                NaN                       NaN                 NaN   
3857                NaN                       NaN               

In [281]:
pd.read_csv("b_scraped.csv")


Brand     Model Generation   Modification (Engine)  \
0     B.Engineering    Edonis     Edonis        3.8 V12 (690 Hp)   
1               BAC      Mono     Mono R  2.5 (340 Hp) Automatic   
2               BAC      Mono       Mono  2.5 (305 Hp) Automatic   
3        BAIC Motor   BJ 2020    BJ 2020             2.4 (87 Hp)   
4        BAIC Motor   BJ 2020    BJ 2020            2.4 (106 Hp)   
...             ...       ...        ...                     ...   
2862            BYD        F3         F3          1.6 i (100 Hp)   
2863            BYD        F6         F6            2.4 (165 Hp)   
2864            BYD        F6         F6            2.0 (140 Hp)   
2865            BYD        F8         F8        2.0 16V (140 Hp)   
2866            BYD  FLYER II   FLYER II           0.8 i (40 Hp)   

     Start of production End of production     Powertrain Architecture  \
0              2002 year         2006 year  Internal Combustion engine   
1              2019 year               NaN  Internal Combustion engine   
2              2016 year         2020 year  Internal Combustion engine   
3              1989 year         2005 year  Internal Combustion engine   
4              1989 year         2005 year  Internal Combustion engine   
...                  ...               ...                         ...   
2862           2005 year         2013 year  Internal Combustion engine   
2863           2007 year         2012 year  Internal Combustion engine   
2864           2007 year         2012 year  Internal Combustion engine   
2865           2009 year         2010 year  Internal Combustion engine   
2866           2005 year         2008 year  Internal Combustion engine   

                   Body type Seats  Doors  ...  \
0                      Coupe     2    2.0  ...   
1                   Roadster     1    NaN  ...   
2                   Roadster     1    NaN  ...   
3     Station wagon (estate)     5    5.0  ...   
4     Station wagon (estate)     5    5.0  ...   
...                      ...   ...    ...  ...   
2862                   Sedan     5    4.0  ...   
2863                   Sedan     5    4.0  ...   
2864                   Sedan     5    4.0  ...   
2865               Cabriolet     2    2.0  ...   
2866               Hatchback     5    5.0  ...   

     Average Energy consumption (NEDC, WLTP equivalent)  \
0                                                   NaN   
1                                                   NaN   
2                                                   NaN   
3                                                   NaN   
4                                                   NaN   
...                                                 ...   
2862                                                NaN   
2863                                                NaN   
2864                                                NaN   
2865                                                NaN   
2866                                                NaN   

     Average Energy consumption (NEDC) Recuperation output  \
0                                  NaN                 NaN   
1                                  NaN                 NaN   
2                                  NaN                 NaN   
3                                  NaN                 NaN   
4                                  NaN                 NaN   
...                                ...                 ...   
2862                               NaN                 NaN   
2863                               NaN                 NaN   
2864                               NaN                 NaN   
2865                               NaN                 NaN   
2866                               NaN                 NaN   

     Average Energy consumption (WLTP) Electric motor 2 Ramp angle  \
0                                  NaN              NaN        NaN   
1                                  NaN              NaN        NaN   
2                                  NaN     

In [283]:
pd.read_csv("z_scraped.csv")


Brand       Model  Generation       Modification (Engine)  \
0     Zacua         MX2         MX2     18 kWh (46 Hp) Electric   
1     Zacua         MX3         MX3     18 kWh (46 Hp) Electric   
2   Zastava          10          10              1.2 8V (60 Hp)   
3   Zastava         101  101 (1100)           1.1 Super (64 Hp)   
4   Zastava         101  101 (1100)                 1.1 (56 Hp)   
..      ...         ...         ...                         ...   
68       ZX  GrandTiger  GrandTiger            2.4 (126 Hp) 4x4   
69       ZX  GrandTiger  GrandTiger            2.4 (126 Hp) 4x2   
70       ZX    Landmark    Landmark            2.4 (126 Hp) 4x4   
71       ZX    Landmark    Landmark  2.4 (126 Hp) 4x2 Automatic   
72       ZX    Landmark    Landmark                2.4 (126 Hp)   

   Start of production     Powertrain Architecture  Body type  Seats Doors  \
0      July, 2017 year      BEV (Electric Vehicle)      Coupe    2.0     2   
1      July, 2017 year      BEV (Electric Vehicle)  Hatchback    2.0     3   
2   October, 2005 year  Internal Combustion engine  Hatchback    5.0     5   
3            1979 year  Internal Combustion engine  Hatchback    NaN   NaN   
4            1975 year  Internal Combustion engine  Hatchback    5.0   3/5   
..                 ...                         ...        ...    ...   ...   
68           2007 year  Internal Combustion engine    Pick-up    5.0     4   
69           2007 year  Internal Combustion engine    Pick-up    5.0     4   
70           2006 year  Internal Combustion engine        SUV    7.0     5   
71           2006 year  Internal Combustion engine        SUV    7.0     5   
72           2006 year  Internal Combustion engine        SUV    7.0     5   

    Performance specs  ... Valvetrain Trunk (boot) space - maximum  \
0   Performance specs  ...        NaN                          NaN   
1   Performance specs  ...        NaN                          NaN   
2   Performance specs  ...        NaN                          NaN   
3   Performance specs  ...        NaN                          NaN   
4   Performance specs  ...       SOHC                          NaN   
..                ...  ...        ...                          ...   
68  Performance specs  ...       DOHC                          NaN   
69  Performance specs  ...       DOHC                          NaN   
70  Performance specs  ...       DOHC                          NaN   
71  Performance specs  ...       DOHC                          NaN   
72  Performance specs  ...       DOHC                          NaN   

   Steering type            Max. weight              Max load  \
0            NaN                    NaN                   NaN   
1            NaN                    NaN                   NaN   
2            NaN                    NaN                   NaN   
3            NaN                    NaN                   NaN   
4            NaN                    NaN                   NaN   
..           ...                    ...                   ...   
68           NaN  2110 kg  4651.75 lbs.  500 kg  1102.31 lbs.   
69           NaN  2110 kg  4651.75 lbs.  500 kg  1102.31 lbs.   
70           NaN  2235 kg  4927.33 lbs.   455 kg  1003.1 lbs.   
71           NaN  2165 kg  4773.01 lbs.   455 kg  1003.1 lbs.   
72           NaN  2125 kg  4684.82 lbs.   455 kg  1003.1 lbs.   

   Acceleration 0 - 200 km/h Ride height (ground clearance)  \
0                        NaN                            NaN   
1                        NaN                            NaN   
2                        NaN                            NaN   
3                        NaN                            NaN   
4                        NaN                            NaN   
..                       ...                            ...   
68                       NaN                            NaN   
69                       NaN                            NaN   
70                       NaN                            NaN   
71          